In [3]:
import tensorflow as tf
import numpy as np
import os
import sys
import time
import cv2

from collections import defaultdict
from io import StringIO
from matplotlib import pyplot as plt
from PIL import Image


In [4]:
# Here are the imports from the object detection module.
from object_detection.utils import label_map_util
from object_detection.utils import visualization_utils as vis_util

In [5]:
flags = tf.app.flags
flags.DEFINE_string('input_video', 'test.mp4', 'Input video to test.')
flags.DEFINE_string('export_model', 'ssd_mobilenet_v1_ship_15000', 'Add your trained model.')
FLAGS = flags.FLAGS

In [6]:
# Model preparation
MODEL_NAME = './object_detection/export_models/ssd_inception_v2_ship_15000'

# Path to frozen detection graph. This is the actual model that is used for the object detection.
PATH_TO_CKPT = MODEL_NAME + '/frozen_inference_graph.pb'

# List of the strings that is used to add correct label for each box.
PATH_TO_LABELS = os.path.join('object_detection/data', 'ship_label_map.pbtxt')

NUM_CLASSES = 1


In [7]:
# Load a (frozen) Tensorflow model into memory.
detection_graph = tf.Graph()
with detection_graph.as_default():
  od_graph_def = tf.GraphDef()
  with tf.gfile.GFile(PATH_TO_CKPT, 'rb') as fid:
    serialized_graph = fid.read()
    od_graph_def.ParseFromString(serialized_graph)
    tf.import_graph_def(od_graph_def, name='')


In [8]:
label_map = label_map_util.load_labelmap(PATH_TO_LABELS)
categories = label_map_util.convert_label_map_to_categories(label_map, max_num_classes=NUM_CLASSES, use_display_name=True)
category_index = label_map_util.create_category_index(categories)

In [9]:
def load_image_into_numpy_array(image):
  (im_width, im_height) = image.size
  return np.array(image.getdata()).reshape(
      (im_height, im_width, 3)).astype(np.uint8)


In [ ]:
# Detection using cv2.
with detection_graph.as_default():
  with tf.Session(graph=detection_graph) as sess:
    # Opencv, Video capture
    cap = cv2.VideoCapture('./test.mp4')

    prevTime = 0  # Frame time variable

    # Recording Video
    fps = 30.0
    width = int(cap.get(3))
    height = int(cap.get(4))
    fcc = cv2.VideoWriter_fourcc('D', 'I', 'V', 'X')
#     recording_video = "rec_{}.avi".format(input_video(test[:-4])) # input_video: video name(sys.args[1])
    out = cv2.VideoWriter('output.avi', fcc, fps, (width, height))

    while True:
      # Opencv, Video capture
      ret, image_np = cap.read()

      # Expand dimensions since the model expects images to have shape: [1, None, None, 3]
      image_np_expanded = np.expand_dims(image_np, axis=0)
      image_tensor = detection_graph.get_tensor_by_name('image_tensor:0')
      # Each box represents a part of the image where a particular object was detected.
      boxes = detection_graph.get_tensor_by_name('detection_boxes:0')
      # Each score represent how level of confidence for each of the objects.
      # Score is shown on the result image, together with the class label.
      scores = detection_graph.get_tensor_by_name('detection_scores:0')
      classes = detection_graph.get_tensor_by_name('detection_classes:0')
      num_detections = detection_graph.get_tensor_by_name('num_detections:0')
      # Actual detection.
      (boxes, scores, classes, num_detections) = sess.run(
          [boxes, scores, classes, num_detections],
          feed_dict={image_tensor: image_np_expanded})
      # Visualization of the results of a detection.
      vis_util.visualize_boxes_and_labels_on_image_array(
          image_np,
          np.squeeze(boxes),
          np.squeeze(classes).astype(np.int32),
          np.squeeze(scores),
          category_index,
          use_normalized_coordinates=True,
          min_score_thresh=.9,
          line_thickness=2)
    
      ################### Data analysis ###################
      print("")
      final_score = np.squeeze(scores)  # scores
      r_count = 0  # counting
      r_score = []  # temp score, <class 'numpy.ndarray'>
      final_category = np.array([category_index.get(i) for i in classes[0]]) # category
      r_category = np.array([])  # temp category
      
      for i in range(100):
        if scores is None or final_score[i] > 0.7:
          r_count = r_count + 1
          r_score = np.append(r_score, final_score[i])
          r_category = np.append(r_category, final_category[i])
      
      if r_count > 0:
        print("Number of bounding boxes: ", r_count)
        print("")
      else:
        print("Not Detect")
        print("")
      for i in range(len(r_score)):  # socre array`s length
        print("Object Num: {} , Category: {} , Score: {}%".format(i+1, r_category[i]['name'], 100*r_score[i]))
        print("")
        final_boxes = np.squeeze(boxes)[i]  # ymin, xmin, ymax, xmax
        xmin = final_boxes[1]
        ymin = final_boxes[0]
        xmax = final_boxes[3]
        ymax = final_boxes[2]
        location_x = (xmax+xmin)/2
        location_y = (ymax+ymin)/2
        # print("final_boxes [ymin xmin ymax xmax]")
        # print("final_boxes", final_boxes)
        print("Location x: {}, y: {}".format(location_x, location_y))
        print("")
      print("+ " * 30 ) 
      #####################################################        

      # Frame
      curTime = time.time()
      sec = curTime - prevTime
      prevTime = curTime
      fps = 1/(sec)
      str = "FPS : %0.1f" % fps

      # Display
      display_model_name = MODEL_NAME.split('/')[2]
      cv2.putText(image_np, display_model_name, (5, 20), cv2.FONT_HERSHEY_PLAIN, 1, (255, 0, 0))
      cv2.putText(image_np, str, (5, 40), cv2.FONT_HERSHEY_PLAIN, 1, (255, 0, 0))
      cv2.imshow('ship detection', cv2.resize(image_np, (1300,800)))

      # Recording Video
      out.write(image_np)

      if cv2.waitKey(1) & 0xFF == ord('q'):
        cv2.destroyAllWindows()
        break


In [10]:
def pipeline(image):
#     detection_graph = tf.Graph()
#     with detection_graph.as_default():
#       od_graph_def = tf.GraphDef()
#       with tf.gfile.GFile(PATH_TO_CKPT, 'rb') as fid:
#         serialized_graph = fid.read()
#         od_graph_def.ParseFromString(serialized_graph)
#         tf.import_graph_def(od_graph_def, name='')
    #global detection_graph
    with detection_graph.as_default():
          with tf.Session(graph=detection_graph) as sess:
            
                image_np = np.asarray(image)
                image_np_expanded = np.expand_dims(image_np, axis=0)
                image_tensor = detection_graph.get_tensor_by_name('image_tensor:0')
                # Each box represents a part of the image where a particular object was detected.
                boxes = detection_graph.get_tensor_by_name('detection_boxes:0')
                # Each score represent how level of confidence for each of the objects.
                # Score is shown on the result image, together with the class label.
                scores = detection_graph.get_tensor_by_name('detection_scores:0')

                classes = detection_graph.get_tensor_by_name('detection_classes:0')
                num_detections = detection_graph.get_tensor_by_name('num_detections:0')
                # Actual detection.
                (boxes, scores, classes, num_detections) = sess.run(
                  [boxes, scores, classes, num_detections],
                  feed_dict={image_tensor: image_np_expanded})
                # Visualization of the results of a detection.
                vis_util.visualize_boxes_and_labels_on_image_array(
                  image_np,
                  np.squeeze(boxes),
                  np.squeeze(classes).astype(np.int32),
                  np.squeeze(scores),
                  category_index,
                  use_normalized_coordinates=True,
                  min_score_thresh=.9,
                  line_thickness=2)

                ################### Data analysis ###################
                print("")
                final_score = np.squeeze(scores)  # scores
                r_count = 0  # counting
                r_score = []  # temp score, <class 'numpy.ndarray'>
                final_category = np.array([category_index.get(i) for i in classes[0]]) # category
                r_category = np.array([])  # temp category

                for i in range(100):
                    if scores is None or final_score[i] > 0.7:
                        r_count = r_count + 1
                        r_score = np.append(r_score, final_score[i])
                        r_category = np.append(r_category, final_category[i])

                if r_count > 0:
                    print("Number of bounding boxes: ", r_count)
                    print("")
                else:
                    print("Not Detect")
                    print("")
                for i in range(len(r_score)):  # socre array`s length
                    print("Object Num: {} , Category: {} , Score: {}%".format(i+1, r_category[i]['name'], 100*r_score[i]))
                    print("")
                    final_boxes = np.squeeze(boxes)[i]  # ymin, xmin, ymax, xmax
                    xmin = final_boxes[1]
                    ymin = final_boxes[0]
                    xmax = final_boxes[3]
                    ymax = final_boxes[2]
                    location_x = (xmax+xmin)/2
                    location_y = (ymax+ymin)/2
                    # print("final_boxes [ymin xmin ymax xmax]")
                    # print("final_boxes", final_boxes)
                    print("Location x: {}, y: {}".format(location_x, location_y))
                    print("")
                print("+ " * 30 ) 
                #####################################################       
    return image_np

#                 # Frame
#                 curTime = time.time()
#                 sec = curTime - prevTime
#                 prevTime = curTime
#                 fps = 1/(sec)
#                 str = "FPS : %0.1f" % fps

#                 # Display
#                 display_model_name = MODEL_NAME.split('/')[2]
#                 cv2.putText(image_np, display_model_name, (5, 20), cv2.FONT_HERSHEY_PLAIN, 1, (255, 0, 0))
#                 cv2.putText(image_np, str, (5, 40), cv2.FONT_HERSHEY_PLAIN, 1, (255, 0, 0))
#                 cv2.imshow('ship detection', cv2.resize(image_np, (1300,800)))

#                 # Recording Video
#                 out.write(image_np)

#                 if cv2.waitKey(1) & 0xFF == ord('q'):
#                     cv2.destroyAllWindows()
#                     break


In [11]:

from moviepy.editor import VideoFileClip
vid_output = 'result9.mp4'
clip = VideoFileClip("test.mp4")
vid = clip.fl_image(pipeline)
vid.write_videofile(vid_output, audio=False)


Number of bounding boxes:  1

Object Num: 1 , Category: ship , Score: 95.57943940162659%

Location x: 0.33327630162239075, y: 0.40351414680480957

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 
[MoviePy] >>>> Building video result9.mp4
[MoviePy] Writing video result9.mp4


  0%|          | 1/398 [00:01<07:11,  1.09s/it]


Not Detect

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 


  1%|          | 2/398 [00:02<07:10,  1.09s/it]


Number of bounding boxes:  1

Object Num: 1 , Category: ship , Score: 94.43159699440002%

Location x: 0.3330706059932709, y: 0.40283888578414917

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 


...

100%|█████████▉| 397/398 [07:28<00:01,  1.13s/it]


Number of bounding boxes:  1

Object Num: 1 , Category: ship , Score: 82.91124105453491%

Location x: 0.8968379497528076, y: 0.4653843939304352

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 


100%|██████████| 398/398 [07:29<00:00,  1.13s/it]


Number of bounding boxes:  1

Object Num: 1 , Category: ship , Score: 97.92630076408386%

Location x: 0.8941998481750488, y: 0.4791402220726013

+ + + + + + + + + + + + + + + + + + + + + + + + + + + + + + 


[MoviePy] Done.
[MoviePy] >>>> Video ready: result9.mp4 



In [14]:

import io# import # import 
import base64
from IPython.display import HTML

video = io.open('result9.mp4', 'r+b').read()
encoded = base64.b64encode(video)
HTML(data='''<video alt="test" controls>
                <source src="data:video/mp4;base64,{0}" type="video/mp4" />
             </video>'''.format(encoded.decode('ascii')))